# 라이브러리 설치, 모델 다운로드

In [ ]:
!pip install numpy insightface pillow opencv-python matplotlib

In [ ]:
!pip install ort-nightly-gpu --index-url=https://aiinfra.pkgs.visualstudio.com/PublicPackages/_packaging/ort-cuda-12-nightly/pypi/simple/ #코랩 또는 cuda 12
#!pip install onnxruntime #cpu 사용
#!pip install onnxruntime-gpu --extra-index-url https://aiinfra.pkgs.visualstudio.com/PublicPackages/_packaging/onnxruntime-cuda-12/pypi/simple/ # cuda12
#!pip install onnxruntime-gpu #cuda 12 미만

In [ ]:
!wget https://huggingface.co/ezioruan/inswapper_128.onnx/resolve/main/inswapper_128.onnx?download=true -O inswapper_128.onnx

# 파이썬 코드

In [ ]:
from PIL import Image
import cv2
import matplotlib.pyplot as plt
from insightface.app import FaceAnalysis
import insightface

app = FaceAnalysis(allowed_modules=['detection','recognition'], providers=['CPUExecutionProvider', 'CUDAExecutionProvider'])
app.prepare(ctx_id=0, det_thresh=0.5, det_size=(640, 640))

swapper = insightface.model_zoo.get_model('inswapper_128.onnx',providers=['CPUExecutionProvider', 'CUDAExecutionProvider'])

In [5]:
img1 = cv2.imread('sg.jpg')
faces1 = app.get(img1)
img2 = cv2.imread('sq.webp')
faces2 = app.get(img2)

## 얼굴 탐지 시각화

In [ ]:
def faceplot(img, faces):
    l = len(faces)
    x = l//5+1
    fig,axes=plt.subplots(nrows=x,ncols=5,figsize=(10,x*2))

    if x==1:
        for col in range(5):
            ax=axes[col]
            if col < l:
                box = faces[col].bbox
                roi = img[int(box[1]):int(box[3]), int(box[0]):int(box[2])]
                roi = cv2.cvtColor(roi,cv2.COLOR_BGR2RGB)
                ax.imshow(roi)
                ax.set_xlabel(str(col),fontsize=20)
            else:
                fig.delaxes(ax)
    else:
        for row in range(x):
            for col in range(5):
                idx = row*5+col
                ax=axes[row][col]
                if idx < l:
                    box = faces[idx].bbox
                    roi = img[int(box[1]):int(box[3]), int(box[0]):int(box[2])]
                    roi = cv2.cvtColor(roi,cv2.COLOR_BGR2RGB)
                    ax.imshow(roi)
                    ax.set_xlabel(str(idx),fontsize=20)
                else:
                    fig.delaxes(ax)
    plt.tight_layout()
    plt.show()

In [ ]:
faceplot(img1,faces1)

In [ ]:
faceplot(img2,faces2)

## 얼굴 바꾸기

In [ ]:
result = swapper.get(img2, faces2[6], faces1[2], paste_back=True)

temp = cv2.cvtColor(result, cv2.COLOR_BGR2RGB)
rimg = Image.fromarray(temp)
display(rimg)

In [ ]:
def faceswap(img,faces1,faces2,l):
    for t in l:
        img = swapper.get(img, faces1[t[0]], faces2[t[1]], paste_back=True)

    temp = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    rimg = Image.fromarray(temp)
    display(rimg)

In [ ]:
faceswap(img2,faces2,faces1,[(6,2),(0,2),(4,1),(5,1),(1,0),(2,0),(3,0),(7,0)])

## 임베딩벡터 만들어 합성하기

In [ ]:
import numpy as np
from insightface.app.common import Face

vector = np.random.normal(loc=0.0, scale=1.0, size=512).astype(np.float32)

base_face = faces1[0].copy()
random_face = Face(**base_face)
random_face.embedding = vector

In [ ]:
result = swapper.get(img2, faces2[1], random_face, paste_back=True)

temp = cv2.cvtColor(result, cv2.COLOR_BGR2RGB)
rimg = Image.fromarray(temp)
display(rimg)

# 이미지 품질 개선

In [ ]:
!wget https://github.com/TencentARC/GFPGAN/releases/download/v1.3.0/GFPGANv1.4.pth -O GFPGANv1.4.pth
!wget https://github.com/xinntao/Real-ESRGAN/releases/download/v0.2.5.0/realesr-general-x4v3.pth -O realesr-general-x4v3.pth

In [ ]:
!pip install basicsr
!pip install facexlib
!pip install gfpgan
!pip install realesrgan

In [9]:
from basicsr.archs.srvgg_arch import SRVGGNetCompact
from gfpgan.utils import GFPGANer
from realesrgan.utils import RealESRGANer
import torch

In [ ]:
model = SRVGGNetCompact(num_in_ch=3, num_out_ch=3, num_feat=64, num_conv=32, upscale=4, act_type='prelu')
model_path = 'realesr-general-x4v3.pth'
half = True if torch.cuda.is_available() else False
upsampler = RealESRGANer(scale=4, model_path=model_path, model=model, tile=0, tile_pad=10, pre_pad=0, half=half)

In [ ]:
face_enhancer = GFPGANer(model_path='GFPGANv1.4.pth', upscale=2, arch='clean', channel_multiplier=2, bg_upsampler=upsampler)

## opencv로 불러온 이미지에 적용

In [ ]:
cropped_faces, restored_faces, restored_img = face_enhancer.enhance(img2, has_aligned=False, only_center_face=False, paste_back=True)

In [ ]:
temp1 = cv2.cvtColor(cropped_faces[0], cv2.COLOR_BGR2RGB)
rimg1 = Image.fromarray(temp1)
display(rimg1)

In [ ]:
temp2 = cv2.cvtColor(restored_faces[0], cv2.COLOR_BGR2RGB)
rimg2 = Image.fromarray(temp2)
display(rimg2)

In [ ]:
temp3 = cv2.cvtColor(restored_img, cv2.COLOR_BGR2RGB)
rimg3 = Image.fromarray(temp3)
display(rimg3)

## 합성 결과에 이용

In [12]:
def faceswap2(img,faces1,faces2,l):
    for t in l:
        img = swapper.get(img, faces1[t[0]], faces2[t[1]], paste_back=True)

    return img

In [14]:
result = faceswap2(img2,faces2,faces1,[(6,2),(0,2),(4,1),(5,1),(1,0),(2,0),(3,0),(7,0)])

In [20]:
_,_,restored_img = face_enhancer.enhance(result, has_aligned=False, only_center_face=False, paste_back=True)

In [ ]:
temp4 = cv2.cvtColor(restored_img, cv2.COLOR_BGR2RGB)
rimg4 = Image.fromarray(temp4)
display(rimg4)